# <center>  **Define the best location for a steakhouse in Rio** </center>
&nbsp; 

<p> 
   <center> <h2>Felipe N Santos </h2> </center> </P>
<BR> 
&nbsp; 

<center> <h3> Project as part of the IBM Capstone in 
<br> 
&nbsp; 
<p> <center> Applied Data Science final assignment  </h3>  </center>
&nbsp;

# Importing Libraries

In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
import lxml
from geopy.geocoders import Nominatim
import geopandas as gpd
from geopandas import GeoDataFrame
from shapely.geometry import Point
import requests
import matplotlib.cm as cm
import matplotlib.colors as colors
import seaborn as sns
sns.set_style("darkgrid", {'legend.frameon':True, 'figure.facecolor':'white', 'axes.facecolor': '#ededed' })
sns.set()
import folium
from sklearn.cluster import KMeans

print('Libraries imported.')

Libraries imported.


# Reading the neighbourhood list
&nbsp;
## Retrieving and formatting the Data

In [2]:
with open("Limite_de_Bairros.csv") as file:
    dfp = (pd.read_csv(file))
    n_list = list(dfp["NOME"].astype(str))
    for l in range(len(n_list)):
        n_list[l] = n_list[l].rstrip(" ")
    df_l = pd.DataFrame(n_list)
    df_final = pd.DataFrame(columns=['Neighbourhood',"Latitude", "Longitude"]) 
    for b in df_l[0]:
        address = b +", Rio de janeiro, RJ, Brazil"
        geolocator = Nominatim(user_agent="http")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        df_final = df_final.append({'Neighbourhood':address,
            'Latitude':latitude,
            'Longitude':longitude}, ignore_index=True)
df_final

Neighbourhood   Latitude  Longitude
0                  Paquetá, Rio de janeiro, RJ, Brazil -22.758926 -43.109199
1         Freguesia (Ilha), Rio de janeiro, RJ, Brazil -22.785060 -43.169453
2                Bancários, Rio de janeiro, RJ, Brazil -22.791759 -43.180966
3                   Galeão, Rio de janeiro, RJ, Brazil -22.807506 -43.235521
4                     Tauá, Rio de janeiro, RJ, Brazil -22.797749 -43.186748
5               Portuguesa, Rio de janeiro, RJ, Brazil -22.799960 -43.206817
6                   Moneró, Rio de janeiro, RJ, Brazil -22.796495 -43.197406
7            Vigário Geral, Rio de janeiro, RJ, Brazil -22.809533 -43.309704
8                   Cocotá, Rio de janeiro, RJ, Brazil -22.805005 -43.180546
9           Jardim América, Rio de janeiro, RJ, Brazil -22.810005 -43.323212
10          Jardim Carioca, Rio de janeiro, RJ, Brazil -22.805249 -43.193195
11                  Pavuna, Rio de janeiro, RJ, Brazil -22.812193 -43.359281
12                Cordovil, Rio de janeiro, RJ, Brazil -22.819438 -43.291591
13        Jardim Guanabara, Rio de janeiro, RJ, Brazil -22.812836 -43.200779
14         Parada de Lucas, Rio de janeiro, RJ, Brazil -22.816702 -43.301210
15         Parque Colúmbia, Rio de janeiro, RJ, Brazil -22.813891 -43.342498
16       Praia da Bandeira, Rio de janeiro, RJ, Brazil -22.810408 -43.179895
17          Penha Circular, Rio de janeiro, RJ, Brazil -22.832642 -43.284223
18                  Cacuia, Rio de janeiro, RJ, Brazil -22.821703 -43.183792
19                   Irajá, Rio de janeiro, RJ, Brazil -22.835113 -43.323362
20                Anchieta, Rio de janeiro, RJ, Brazil -22.823190 -43.399107
21                   Acari, Rio de janeiro, RJ, Brazil -22.822153 -43.340674
22            Pitangueiras, Rio de janeiro, RJ, Brazil -22.817128 -43.179954
23            Costa Barros, Rio de janeiro, RJ, Brazil -22.824700 -43.369839
24            Brás de Pina, Rio de janeiro, RJ, Brazil -22.831888 -43.297731
25                   Penha, Rio de janeiro, RJ, Brazil -22.838113 -43.276445
26                   Zumbi, Rio de janeiro, RJ, Brazil -22.821278 -43.175861
27                 Ribeira, Rio de janeiro, RJ, Brazil -22.825240 -43.170591
28             Coelho Neto, Rio de janeiro, RJ, Brazil -22.831874 -43.342919
29               Guadalupe, Rio de janeiro, RJ, Brazil -22.837621 -43.375161
30         Parque Anchieta, Rio de janeiro, RJ, Brazil -22.835169 -43.415583
31            Barros Filho, Rio de janeiro, RJ, Brazil -22.834886 -43.363188
32            Vista Alegre, Rio de janeiro, RJ, Brazil -22.829624 -43.315128
33   Ricardo de Albuquerque, Rio de janeiro, RJ, Br... -22.838092 -43.396344
34                 Colégio, Rio de janeiro, RJ, Brazil -22.924312 -43.176170
35          Honório Gurgel, Rio de janeiro, RJ, Brazil -22.846575 -43.356129
36                  Olaria, Rio de janeiro, RJ, Brazil -22.304596 -42.540627
37           Vila da Penha, Rio de janeiro, RJ, Brazil -22.843507 -43.310058
38                    Maré, Rio de janeiro, RJ, Brazil -22.859237 -43.242573
39            Vila Militar, Rio de janeiro, RJ, Brazil -22.860348 -43.402893
40    Cidade Universitária, Rio de janeiro, RJ, Brazil -22.855823 -43.230958
41           Rocha Miranda, Rio de janeiro, RJ, Brazil -22.850347 -43.346305
42                   Ramos, Rio de janeiro, RJ, Brazil -22.851976 -43.255569
43                Realengo, Rio de janeiro, RJ, Brazil -22.877274 -43.430103
44             Vila Kosmos, Rio de janeiro, RJ, Brazil -22.853597 -43.303202
45         Marechal Hermes, Rio de janeiro, RJ, Brazil -22.859966 -43.370456
46     Vicente de Carvalho, Rio de janeiro, RJ, Brazil -22.857180 -43.315789
47               Paciência, Rio de janeiro, RJ, Brazil -22.898700 -43.636956
48       Engenho da Rainha, Rio de janeiro, RJ, Brazil -22.862650 -43.293787
49      Complexo do Alemão, Rio de janeiro, RJ, Brazil -22.860610 -43.273751
50                Vaz Lobo, Rio de janeiro, RJ, Brazil -22.858972 -43.327865
51            Padre Miguel, Rio de ja

# Preparing the map

In [3]:
address = 'Rio de janeiro'

geolocator = Nominatim(user_agent="http")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Rio de Janeiro are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Rio de Janeiro are -22.9110137, -43.2093727.


In [4]:
# create map of Rio using latitude and longitude values
map_rio = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, Neighbourhood in zip(df_final['Latitude'], df_final['Longitude'], df_final['Neighbourhood']):
    label = '{}'.format(Neighbourhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_rio)
    
map_rio

## Exploring Rio with Foursquare API

In [488]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 
CLIENT_SECRET:


## Explorating a example location

In [6]:
df_final.loc[159, 'Neighbourhood']

'Bangu, Rio de janeiro, RJ, Brazil'

In [7]:
neighbourhood_latitude = df_final.loc[159, 'Latitude'] # neighbourhood latitude value
neighbourhood_longitude = df_final.loc[159, 'Longitude'] # neighbourhood longitude value

neighbourhood_name = df_final.loc[159, 'Neighbourhood'] # neighboyrhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighbourhood_name, 
                                                               neighbourhood_latitude, 
                                                               neighbourhood_longitude))

Latitude and longitude values of Bangu, Rio de janeiro, RJ, Brazil are -22.8753053, -43.4648805.


In [8]:
# type your answer here


LIMIT = 100 # limit of number of venues returned by Foursquare API



radius = 500 # define radius



url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighbourhood_latitude, 
    neighbourhood_longitude, 
    radius, 
    LIMIT)
url # display URL
 


'https://api.foursquare.com/v2/venues/explore?&client_id=FJH0LPXJCBN14WPMOWICSZECE3P1KNWV4JH2FIBMPZCJFLIE&client_secret=3LXKHC21IYUKN04VQDXGKRPFG0RFUF4KJADF4ST01R2DMCJA&v=20180605&ll=-22.8753053,-43.4648805&radius=500&limit=100'

In [9]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '601323a566386a3570cf2887'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Bangu',
  'headerFullLocation': 'Bangu, Rio de Janeiro',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 41,
  'suggestedBounds': {'ne': {'lat': -22.870805295499995,
    'lng': -43.46000549301421},
   'sw': {'lat': -22.879805304500007, 'lng': -43.46975550698579}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4d1b5ccb11fca0939a849dce',
       'name': "McDonald's",
       'location': {'address': 'Av. Cônego Vasconcelos, 19',
        'lat': -22.875753732131628,
        'lng': -43.46480552705355,
        'labeledLatLngs': [{'label': 'display',
          '

In [10]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [11]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat        lng
0              McDonald's  Fast Food Restaurant -22.875754 -43.464806
1               Smart Fit  Gym / Fitness Center -22.877977 -43.467594
2      Outback Steakhouse            Steakhouse -22.877968 -43.468116
3        Boteco do Manolo                   Bar -22.878357 -43.467320
4  Theatro Bangu Shopping               Theater -22.878738 -43.465797

In [12]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

41 venues were returned by Foursquare.


## Automating and repeating the process for the other neighbourhods

In [13]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [14]:
rio_venues = getNearbyVenues(names=df_final['Neighbourhood'],
                                   latitudes=df_final['Latitude'],
                                   longitudes=df_final['Longitude']
                                  )

Paquetá, Rio de janeiro, RJ, Brazil
Freguesia (Ilha), Rio de janeiro, RJ, Brazil
Bancários, Rio de janeiro, RJ, Brazil
Galeão, Rio de janeiro, RJ, Brazil
Tauá, Rio de janeiro, RJ, Brazil
Portuguesa, Rio de janeiro, RJ, Brazil
Moneró, Rio de janeiro, RJ, Brazil
Vigário Geral, Rio de janeiro, RJ, Brazil
Cocotá, Rio de janeiro, RJ, Brazil
Jardim América, Rio de janeiro, RJ, Brazil
Jardim Carioca, Rio de janeiro, RJ, Brazil
Pavuna, Rio de janeiro, RJ, Brazil
Cordovil, Rio de janeiro, RJ, Brazil
Jardim Guanabara, Rio de janeiro, RJ, Brazil
Parada de Lucas, Rio de janeiro, RJ, Brazil
Parque Colúmbia, Rio de janeiro, RJ, Brazil
Praia da Bandeira, Rio de janeiro, RJ, Brazil
Penha Circular, Rio de janeiro, RJ, Brazil
Cacuia, Rio de janeiro, RJ, Brazil
Irajá, Rio de janeiro, RJ, Brazil
Anchieta, Rio de janeiro, RJ, Brazil
Acari, Rio de janeiro, RJ, Brazil
Pitangueiras, Rio de janeiro, RJ, Brazil
Costa Barros, Rio de janeiro, RJ, Brazil
Brás de Pina, Rio de janeiro, RJ, Brazil
Penha, Rio de janei

In [15]:
print(rio_venues.shape)
rio_venues.head()

(2998, 7)


Neighbourhood  Neighbourhood Latitude  \
0  Paquetá, Rio de janeiro, RJ, Brazil              -22.758926   
1  Paquetá, Rio de janeiro, RJ, Brazil              -22.758926   
2  Paquetá, Rio de janeiro, RJ, Brazil              -22.758926   
3  Paquetá, Rio de janeiro, RJ, Brazil              -22.758926   
4  Paquetá, Rio de janeiro, RJ, Brazil              -22.758926   

   Neighbourhood Longitude               Venue  Venue Latitude  \
0               -43.109199  Praia da Moreninha      -22.757123   
1               -43.109199   Praia dos Tamoios      -22.761351   
2               -43.109199          Hotel Lido      -22.762042   
3               -43.109199      Tia Leleta Bar      -22.760765   
4               -43.109199   Quintal da Regina      -22.760820   

   Venue Longitude        Venue Category  
0       -43.110195                 Beach  
1       -43.107832                 Beach  
2       -43.110205        Boarding House  
3       -43.108334  Brazilian Restaurant  
4       -43.108288                   Bar

In [16]:
rio_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                
Abolição, Rio de janeiro, RJ, Brazil                                    24   
Acari, Rio de janeiro, RJ, Brazil                                        5   
Alto da Boa Vista, Rio de janeiro, RJ, Brazil                            2   
Anchieta, Rio de janeiro, RJ, Brazil                                    12   
Andaraí, Rio de janeiro, RJ, Brazil                                     16   
Anil, Rio de janeiro, RJ, Brazil                                        17   
Bancários, Rio de janeiro, RJ, Brazil                                   24   
Bangu, Rio de janeiro, RJ, Brazil                                       41   
Barra da Tijuca, Rio de janeiro, RJ, Brazil                             12   
Barros Filho, Rio de janeiro, RJ, Brazil                                 4   
Benfica, Rio de janeiro, RJ, Brazil                                     20   
Bento Ribeiro, Rio de janeiro, RJ, Brazil                                9   
Bonsucesso, Rio de janeiro, RJ, Brazil                                  32   
Botafogo, Rio de janeiro, RJ, Brazil                                    48   
Brás de Pina, Rio de janeiro, RJ, Brazil                                 5   
Cachambi, Rio de janeiro, RJ, Brazil                                    25   
Cacuia, Rio de janeiro, RJ, Brazil                                       2   
Caju, Rio de janeiro, RJ, Brazil                                         5   
Camorim, Rio de janeiro, RJ, Brazil                                      2   
Campinho, Rio de janeiro, RJ, Brazil                                    22   
Campo Grande, Rio de janeiro, RJ, Brazil                                36   
Campo dos Afonsos, Rio de janeiro, RJ, Brazil                            4   
Cascadura, Rio de janeiro, RJ, Brazil                                   22   
Catete, Rio de janeiro, RJ, Brazil                                      34   
Catumbi, Rio de janeiro, RJ, Brazil                                      4   
Cavalcanti, Rio de janeiro, RJ, Brazil                                   7   
Centro, Rio de janeiro, RJ, Brazil                                      23   
Cidade Nova, Rio de janeiro, RJ, Brazil                                 45   
Cidade Universitária, Rio de janeiro, RJ, Brazil                         4   
Cidade de Deus, Rio de janeiro, RJ, Brazil                               4   
Cocotá, Rio de janeiro, RJ, Brazil                                      10   
Coelho Neto, Rio de janeiro, RJ, Brazil                                 10   
Colégio, Rio de janeiro, RJ, Brazil                                     74   
Complexo do Alemão, Rio de janeiro, RJ, Brazil                           7   
Copacabana, Rio de janeiro, RJ, Brazil                                 100   
Cordovil, Rio de janeiro, RJ, Brazil                                    13   
Cosme Velho, Rio de janeiro, RJ, Brazil                                 13   
Cosmos, Rio de janeiro, RJ, Brazil                                      10   
Costa Barros, Rio de janeiro, RJ, Brazil                                 4   
Curicica, Rio de janeiro, RJ, Brazil                                    20   
Del Castilho, Rio de janeiro, RJ, Brazil                                86   
Deodoro, Rio de janeiro, RJ, Brazil                                      4   
Encantado, Rio de janeiro, RJ, Brazil                                    4   
Engenheiro Leal, Rio de janeiro, RJ, Brazil                              5   
Engenho Novo, Rio de janeiro, RJ, Brazil                                 6   
Engenho da Rainha, Rio de janeiro, RJ, Brazil                            4   
Engenho de Dentro, Rio de janeiro, RJ, Brazil                           25   
Estácio, Rio de janeiro, RJ, Brazil                                     23   
Flamengo, Rio de janeiro, RJ, Brazil                                    79   
Freguesia (Ilha), Rio de janeiro, RJ, Brazil                             1

## Analyzing the neighbourhoods by venues types

In [18]:
print('There are {} uniques categories.'.format(len(rio_venues['Venue Category'].unique())))

There are 287 uniques categories.


In [19]:
# one hot encoding
rio_onehot = pd.get_dummies(rio_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
rio_onehot['Neighbourhood'] = rio_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [rio_onehot.columns[-1]] + list(rio_onehot.columns[:-1])
rio_onehot = rio_onehot[fixed_columns]

rio_onehot.sample(10)

Neighbourhood  ATM  Acai House  \
110    Jardim América, Rio de janeiro, RJ, Brazil    0           0   
1293            Méier, Rio de janeiro, RJ, Brazil    0           0   
682        Bonsucesso, Rio de janeiro, RJ, Brazil    0           0   
2059         Flamengo, Rio de janeiro, RJ, Brazil    0           0   
1714         Maracanã, Rio de janeiro, RJ, Brazil    0           0   
1240    Vasco da Gama, Rio de janeiro, RJ, Brazil    0           0   
2915     Campo Grande, Rio de janeiro, RJ, Brazil    0           0   
601   Marechal Hermes, Rio de janeiro, RJ, Brazil    0           0   
827      Higienópolis, Rio de janeiro, RJ, Brazil    0           0   
884      Del Castilho, Rio de janeiro, RJ, Brazil    0           0   

      Accessories Store  Adult Boutique  American Restaurant  Arcade  \
110                   0               0                    0       0   
1293                  0               0                    0       0   
682                   0               0                    0       0   
2059                  0               0                    0       0   
1714                  0               0                    0       0   
1240                  0               0                    0       0   
2915                  0               0                    0       0   
601                   0               0                    0       0   
827                   0               0                    0       0   
884                   0               0                    0       0   

      Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
110                        0            0           0                    0   
1293                       0            0           0                    0   
682                        0            0           0                    0   
2059                       0            0           0                    0   
1714                       0            0           0                    0   
1240                       0            0           0                    0   
2915                       0            0           0                    0   
601                        0            0           0                    0   
827                        0            0           0                    0   
884                        0            0           0                    0   

      Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
110                      0                 0                   0            0   
1293                     0                 0                   0            0   
682                      0                 0                   0            0   
2059                     0                 0                   0            0   
1714                     0                 0                   0            0   
1240                     0                 0                   0            0   
2915                     0                 0                   0            0   
601                      0                 0                   0            0   
827                      0                 0                   0            0   
884                      0                 0                   0            0   

      Auto Workshop  BBQ Joint  Bagel Shop  Bakery  Bar  Basketball Court  \
110               0          0           0       0    0                 0   
1293              0          0           0       0    1                 0   
682               0          0           0       0    0                 0   
2059              0          0           0       0    1                 0   
1714              0          0           0       0    0                 0   
1240              0          0           0       0    0                 0   
2915              0          0           0       0    0                 0   
601               0          0           0       0    0                 0   
827               0         

In [20]:
rio_onehot.shape

(2998, 288)

In [21]:
rio_grouped = rio_onehot.groupby('Neighbourhood').mean().reset_index()
rio_grouped

Neighbourhood     ATM  Acai House  \
0                 Abolição, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
1                    Acari, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
2        Alto da Boa Vista, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
3                 Anchieta, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
4                  Andaraí, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
5                     Anil, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
6                Bancários, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
7                    Bangu, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
8          Barra da Tijuca, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
9             Barros Filho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
10                 Benfica, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
11           Bento Ribeiro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
12              Bonsucesso, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
13                Botafogo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
14            Brás de Pina, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
15                Cachambi, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
16                  Cacuia, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
17                    Caju, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
18                 Camorim, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
19                Campinho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
20            Campo Grande, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
21       Campo dos Afonsos, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
22               Cascadura, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
23                  Catete, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
24                 Catumbi, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
25              Cavalcanti, Rio de janeiro, RJ, Brazil  0.0000    0.142857   
26                  Centro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
27             Cidade Nova, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
28    Cidade Universitária, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
29          Cidade de Deus, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
30                  Cocotá, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
31             Coelho Neto, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
32                 Colégio, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
33      Complexo do Alemão, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
34              Copacabana, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
35                Cordovil, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
36             Cosme Velho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
37                  Cosmos, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
38            Costa Barros, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
39                Curicica, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
40            Del Castilho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
41                 Deodoro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
42               Encantado, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
43         Engenheiro Leal, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
44            Engenho Novo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
45       Engenho da Rainha, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
46       Engenho de Dentro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
47                 Estácio, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
48                Flamengo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
49        Freguesia (Ilha), Rio de janeiro, RJ, Brazil  0.0000    0.000000   
50   Freguesia (Jacarepaguá), Rio de janeiro, RJ, B...  0.0000 

### Finding the most common venues for each neibourhoods

In [22]:
rio_grouped = rio_onehot.groupby('Neighbourhood').mean().reset_index()
rio_grouped

Neighbourhood     ATM  Acai House  \
0                 Abolição, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
1                    Acari, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
2        Alto da Boa Vista, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
3                 Anchieta, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
4                  Andaraí, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
5                     Anil, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
6                Bancários, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
7                    Bangu, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
8          Barra da Tijuca, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
9             Barros Filho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
10                 Benfica, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
11           Bento Ribeiro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
12              Bonsucesso, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
13                Botafogo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
14            Brás de Pina, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
15                Cachambi, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
16                  Cacuia, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
17                    Caju, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
18                 Camorim, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
19                Campinho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
20            Campo Grande, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
21       Campo dos Afonsos, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
22               Cascadura, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
23                  Catete, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
24                 Catumbi, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
25              Cavalcanti, Rio de janeiro, RJ, Brazil  0.0000    0.142857   
26                  Centro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
27             Cidade Nova, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
28    Cidade Universitária, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
29          Cidade de Deus, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
30                  Cocotá, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
31             Coelho Neto, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
32                 Colégio, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
33      Complexo do Alemão, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
34              Copacabana, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
35                Cordovil, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
36             Cosme Velho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
37                  Cosmos, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
38            Costa Barros, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
39                Curicica, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
40            Del Castilho, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
41                 Deodoro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
42               Encantado, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
43         Engenheiro Leal, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
44            Engenho Novo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
45       Engenho da Rainha, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
46       Engenho de Dentro, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
47                 Estácio, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
48                Flamengo, Rio de janeiro, RJ, Brazil  0.0000    0.000000   
49        Freguesia (Ilha), Rio de janeiro, RJ, Brazil  0.0000    0.000000   
50   Freguesia (Jacarepaguá), Rio de janeiro, RJ, B...  0.0000 

In [23]:
num_top_venues = 5

for hood in rio_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = rio_grouped[rio_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abolição, Rio de janeiro, RJ, Brazil----
           venue  freq
0      BBQ Joint  0.17
1     Restaurant  0.08
2            Bar  0.08
3  Go Kart Track  0.04
4   Concert Hall  0.04


----Acari, Rio de janeiro, RJ, Brazil----
            venue  freq
0    Churrascaria   0.2
1     Pizza Place   0.2
2          Market   0.2
3    Soccer Field   0.2
4  Ice Cream Shop   0.2


----Alto da Boa Vista, Rio de janeiro, RJ, Brazil----
            venue  freq
0        Mountain   0.5
1  Scenic Lookout   0.5
2             ATM   0.0
3       Pet Store   0.0
4     Pizza Place   0.0


----Anchieta, Rio de janeiro, RJ, Brazil----
                   venue  freq
0                  Plaza  0.33
1         Farmers Market  0.08
2                    Gym  0.08
3  General Entertainment  0.08
4            Snack Place  0.08


----Andaraí, Rio de janeiro, RJ, Brazil----
                  venue  freq
0                Bakery  0.19
1            Restaurant  0.12
2                   Pub  0.06
3  Brazilian Restaurant  0.06


                  venue  freq
0  Brazilian Restaurant  0.13
1                   Bar  0.08
2    Athletics & Sports  0.07
3                 Plaza  0.05
4                 Track  0.05


----Grajaú, Rio de janeiro, RJ, Brazil----
         venue  freq
0        Trail   1.0
1     Platform   0.0
2  Planetarium   0.0
3  Pizza Place   0.0
4         Pier   0.0


----Grumari, Rio de janeiro, RJ, Brazil----
               venue  freq
0              Beach   1.0
1                ATM   0.0
2  Outdoor Sculpture   0.0
3        Pizza Place   0.0
4               Pier   0.0


----Guadalupe, Rio de janeiro, RJ, Brazil----
                  venue  freq
0          Burger Joint  0.23
1  Fast Food Restaurant  0.08
2           Beer Garden  0.08
3           Snack Place  0.08
4           Pizza Place  0.08


----Gávea, Rio de janeiro, RJ, Brazil----
                  venue  freq
0                Bakery  0.14
1           Art Gallery  0.14
2                  Park  0.07
3  Brazilian Restaurant  0.07
4           Film St

                     venue  freq
0             Soccer Field  0.25
1      Japanese Restaurant  0.08
2              Pizza Place  0.08
3  Health & Beauty Service  0.08
4                      Bar  0.08


----Penha, Rio de janeiro, RJ, Brazil----
                               venue  freq
0               Gym / Fitness Center  0.13
1                          Drugstore  0.07
2                         Print Shop  0.07
3                               Café  0.07
4  Southeastern Brazilian Restaurant  0.07


----Piedade, Rio de janeiro, RJ, Brazil----
            venue  freq
0  Sandwich Place   0.2
1            Food   0.1
2     Pizza Place   0.1
3       BBQ Joint   0.1
4   Hot Dog Joint   0.1


----Pilares, Rio de janeiro, RJ, Brazil----
                    venue  freq
0              Food Truck  0.15
1  Furniture / Home Store  0.08
2             Supermarket  0.08
3             Music Venue  0.08
4                  Bakery  0.08


----Pitangueiras, Rio de janeiro, RJ, Brazil----
                venue

                  venue  freq
0                 Beach   0.1
1   Japanese Restaurant   0.1
2           Sports Club   0.1
3  Gym / Fitness Center   0.1
4                 Plaza   0.1


----Água Santa, Rio de janeiro, RJ, Brazil----
                    venue  freq
0            Soccer Field  0.33
1  Furniture / Home Store  0.33
2         Paintball Field  0.33
3               Rest Area  0.00
4             Pizza Place  0.00




In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [25]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = rio_grouped['Neighbourhood']

for ind in np.arange(rio_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(rio_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue  \
0           Abolição, Rio de janeiro, RJ, Brazil             BBQ Joint   
1              Acari, Rio de janeiro, RJ, Brazil          Churrascaria   
2  Alto da Boa Vista, Rio de janeiro, RJ, Brazil              Mountain   
3           Anchieta, Rio de janeiro, RJ, Brazil                 Plaza   
4            Andaraí, Rio de janeiro, RJ, Brazil                Bakery   

  2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0            Restaurant                   Bar          Go Kart Track   
1           Pizza Place                Market           Soccer Field   
2        Scenic Lookout                   ATM              Pet Store   
3        Farmers Market                   Gym  General Entertainment   
4            Restaurant                   Pub   Brazilian Restaurant   

  5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0          Concert Hall                Bakery  Portuguese Restaurant   
1        Ice Cream Shop                   ATM               Pharmacy   
2           Pizza Place                  Pier               Pie Shop   
3           Snack Place  Fast Food Restaurant                 Church   
4              Mountain                   Bar             Bagel Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0        Gymnastics Gym           Pizza Place            Snack Place  
1           Planetarium                  Pier               Pie Shop  
2    Photography Studio              Pharmacy            Pet Service  
3           Sports Club       Border Crossing    Peruvian Restaurant  
4        Cosmetics Shop                 Plaza       Botanical Garden

## Clustering Neghbourhoods

In [26]:
# set number of clusters
kclusters = 5

rio_grouped_clustering = rio_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(rio_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 3, 3, 3, 3, 3, 3, 3, 3, 3], dtype=int32)

In [27]:
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_, allow_duplicates=True)

rio_merged = df_final


# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighbourhood
rio_merged = rio_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

rio_merged.sample(20) # check the last columns!

Neighbourhood   Latitude  Longitude  \
140               Leme, Rio de janeiro, RJ, Brazil -22.961704 -43.166904   
56        Tomás Coelho, Rio de janeiro, RJ, Brazil -22.867698 -43.306088   
66          Manguinhos, Rio de janeiro, RJ, Brazil -22.879676 -43.250888   
48   Engenho da Rainha, Rio de janeiro, RJ, Brazil -22.862650 -43.293787   
118          Pechincha, Rio de janeiro, RJ, Brazil -22.928988 -43.353419   
58           Madureira, Rio de janeiro, RJ, Brazil -22.871658 -43.337198   
126        Cosme Velho, Rio de janeiro, RJ, Brazil -22.941514 -43.200624   
120             Catete, Rio de janeiro, RJ, Brazil -22.926920 -43.180219   
109        Vila Isabel, Rio de janeiro, RJ, Brazil -22.915222 -43.247263   
80         Jacarezinho, Rio de janeiro, RJ, Brazil -22.887507 -43.257879   
100       Engenho Novo, Rio de janeiro, RJ, Brazil -22.909094 -43.267838   
21               Acari, Rio de janeiro, RJ, Brazil -22.822153 -43.340674   
65        Higienópolis, Rio de janeiro, RJ, Brazil -22.873999 -43.261368   
93              Gamboa, Rio de janeiro, RJ, Brazil -22.897749 -43.192904   
83             Benfica, Rio de janeiro, RJ, Brazil -22.892297 -43.240341   
141              Lagoa, Rio de janeiro, RJ, Brazil -22.962466 -43.202488   
123          Guaratiba, Rio de janeiro, RJ, Brazil -22.990584 -43.584923   
142          Itanhangá, Rio de janeiro, RJ, Brazil -22.987091 -43.304938   
59        Osvaldo Cruz, Rio de janeiro, RJ, Brazil -22.870527 -43.350194   
69        Del Castilho, Rio de janeiro, RJ, Brazil -22.879562 -43.272420   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
140             3.0                 Hotel        Scenic Lookout   
56              3.0       Paintball Field               Factory   
66              3.0         Train Station           Snack Place   
48              0.0  Brazilian Restaurant           Music Venue   
118             3.0                 Plaza     German Restaurant   
58              3.0  Fast Food Restaurant  Brazilian Restaurant   
126             3.0                  Café        History Museum   
120             3.0                 Hotel                Hostel   
109             3.0  Brazilian Restaurant            Food Truck   
80              4.0              Mountain  Gym / Fitness Center   
100             3.0           Pizza Place           Snack Place   
21              3.0          Churrascaria           Pizza Place   
65              4.0          Burger Joint                   Gym   
93              3.0               Factory        History Museum   
83              0.0  Brazilian Restaurant        Lighting Store   
141             3.0  Gym / Fitness Center                 Plaza   
123             NaN                   NaN                   NaN   
142             3.0                Bakery   Japanese Restaurant   
59              3.0           Supermarket  Gym / Fitness Center   
69              3.0  Brazilian Restaurant        Ice Cream Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
140                 Beach    Seafood Restaurant           Pizza Place   
56             Food Truck         Train Station  Gym / Fitness Center   
66                    Gym         Deli / Bodega            Restaurant   
48                 Bakery     Food & Drink Shop           Pastry Shop   
118                Market        Breakfast Spot  Brazilian Restaurant   
58       Department Store     Mobile Phone Shop              Tea Room   
126                 Plaza                Hostel        Breakfast Spot   
120  Brazilian Restaurant                   Bar                Bakery   
109                   Bar          Samba School                 Plaza   
80           Burger Joint              Pharmacy           Pizza Place   
100              Bus Stop                   Gym           Auto Garage   
21                 Market          Soccer Field        Ice Cream Shop   
65         Ice Cream Shop             Pet Store  Gym / Fitness Center   
93   Brazi

### Eliminating null values and transforming cluster data in integer

In [28]:
rio_merged.dropna(inplace=True)
rio_merged['Cluster Labels'] = rio_merged['Cluster Labels'].astype(int)
rio_merged.sample(20)

Neighbourhood   Latitude  Longitude  \
143               Gávea, Rio de janeiro, RJ, Brazil -22.981424 -43.238324   
100        Engenho Novo, Rio de janeiro, RJ, Brazil -22.909094 -43.267838   
138      Vargem Pequena, Rio de janeiro, RJ, Brazil -22.981819 -43.457812   
112        Rio Comprido, Rio de janeiro, RJ, Brazil -22.927945 -43.208857   
29            Guadalupe, Rio de janeiro, RJ, Brazil -22.837621 -43.375161   
45      Marechal Hermes, Rio de janeiro, RJ, Brazil -22.859966 -43.370456   
62       Senador Camará, Rio de janeiro, RJ, Brazil -22.888752 -43.491389   
155                Caju, Rio de janeiro, RJ, Brazil -22.880306 -43.221494   
126         Cosme Velho, Rio de janeiro, RJ, Brazil -22.941514 -43.200624   
159               Bangu, Rio de janeiro, RJ, Brazil -22.875305 -43.464880   
86        Vasco da Gama, Rio de janeiro, RJ, Brazil -22.891522 -43.226720   
95               Centro, Rio de janeiro, RJ, Brazil -22.911014 -43.209373   
129                Urca, Rio de janeiro, RJ, Brazil -22.954074 -43.167973   
158        Campo Grande, Rio de janeiro, RJ, Brazil -22.902953 -43.559129   
12             Cordovil, Rio de janeiro, RJ, Brazil -22.819438 -43.291591   
88      Todos os Santos, Rio de janeiro, RJ, Brazil -22.894563 -43.285060   
90            Encantado, Rio de janeiro, RJ, Brazil -22.897474 -43.304246   
63           Cavalcanti, Rio de janeiro, RJ, Brazil -22.870527 -43.316526   
67      Engenheiro Leal, Rio de janeiro, RJ, Brazil -22.874392 -43.325531   
49   Complexo do Alemão, Rio de janeiro, RJ, Brazil -22.860610 -43.273751   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
143               3                Bakery           Art Gallery   
100               3           Pizza Place           Snack Place   
138               3     Convenience Store                  Farm   
112               0  Brazilian Restaurant           Snack Place   
29                4          Burger Joint  Fast Food Restaurant   
45                3            Food Truck           Snack Place   
62                4          Burger Joint                   ATM   
155               3                   Bar             Speakeasy   
126               3                  Café        History Museum   
159               3  Fast Food Restaurant     Accessories Store   
86                0  Brazilian Restaurant           Snack Place   
95                3                   Bar            Restaurant   
129               3           Pizza Place         Souvenir Shop   
158               3              Pharmacy   Japanese Restaurant   
12                4          Burger Joint  Brazilian Restaurant   
88                3             BBQ Joint            Food Truck   
90                3                   Bar        Farmers Market   
63                3                Bakery           Supermarket   
67                3           Snack Place                   Bar   
49                4         Movie Theater  Fast Food Restaurant   

    3rd Most Common Venue          4th Most Common Venue  \
143                  Park           Brazilian Restaurant   
100              Bus Stop                            Gym   
138            Theme Park           Fast Food Restaurant   
112        Sandwich Place                      Pet Store   
29            Beer Garden                    Snack Place   
45            Pizza Place                          Plaza   
62            Pet Service                    Pizza Place   
155            Street Art                    Bus Station   
126                 Plaza                         Hostel   
159        Clothing Store                     Steakhouse   
86    Sporting Goods Shop  Paper / Office Supplies Store   
95          Train Station                           Café   
129  Brazilian Restaurant                   Tram Station   
158                  Café           Brazilian Restaurant   
12                 Bakery              Food & Drink Shop   
88           Burger Joint           Brazilian Restau

## Visualizing the Clustering in Map

In [487]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(rio_merged['Latitude'], rio_merged['Longitude'], rio_merged['Neighbourhood'], rio_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

# Printing clustering results

In [30]:
rio_merged.loc[rio_merged['Cluster Labels'] == 0, rio_merged.columns[[1] + list(range(5, rio_merged.shape[1]))]]

Latitude              2nd Most Common Venue 3rd Most Common Venue  \
15  -22.813891                         Restaurant           Supermarket   
38  -22.859237                     Breakfast Spot             BBQ Joint   
40  -22.855823                 Chinese Restaurant  Gym / Fitness Center   
47  -22.898700                                ATM           Pet Service   
48  -22.862650                        Music Venue                Bakery   
70  -22.892667                               Food           Pizza Place   
83  -22.892297                     Lighting Store            Restaurant   
85  -22.899318  Northeastern Brazilian Restaurant            Restaurant   
86  -22.891522                        Snack Place   Sporting Goods Shop   
89  -22.893117               Brazilian Restaurant          Burger Joint   
91  -22.899562                     Farmers Market                Bakery   
107 -22.910051                        Snack Place            Restaurant   
112 -22.927945                        Snack Place        Sandwich Place   
114 -22.916626                         Food Truck  Gym / Fitness Center   
136 -22.958287                       Burger Joint        Sandwich Place   
148 -22.988520               Brazilian Restaurant           Pizza Place   

             4th Most Common Venue    5th Most Common Venue  \
15                    Burger Joint              Snack Place   
38                     Pet Service              Pizza Place   
40                           Diner               Restaurant   
47                     Pizza Place                     Pier   
48               Food & Drink Shop              Pastry Shop   
70                       BBQ Joint            Hot Dog Joint   
83            Fast Food Restaurant                      Bar   
85              Italian Restaurant                   Bakery   
86   Paper / Office Supplies Store     Gym / Fitness Center   
89                  Sandwich Place            Grocery Store   
91                  Soccer Stadium                      ATM   
107                    Coffee Shop              Bus Station   
112                      Pet Store                 Mountain   
114                     Nail Salon                 Mountain   
136                          Plaza  Health & Beauty Service   
148               Asian Restaurant           Sandwich Place   

         6th Most Common Venue  7th Most Common Venue  \
15                  Food Stand   Gym / Fitness Center   
38                        Pier               Pie Shop   
40                 Pizza Place                   Park   
47                    Pie Shop     Photography Studio   
48            Pedestrian Plaza  Performing Arts Venue   
70                   Nightclub                    Gym   
83              Sandwich Place  Portuguese Restaurant   
85                 Snack Place            Karaoke Bar   
86              Shipping Store  Portuguese Restaurant   
89         Fried Chicken Joint            Pet Service   
91                 Planetarium            Pizza Place   
107  Middle Eastern Restaurant     Italian Restaurant   
112                     Bakery               Pharmacy   
114                     Bistro          Shopping Mall   
136          Convenience Store                    Gym   
148                      Trail                    Gym   

             8th Most Common Venue   9th Most Common Venue  \
15                       Pet Store                    Pier   
38              Photography Studio                Pharmacy   
40                      Pastelaria             Pastry Shop   
47                        Pharmacy               Pet Store   
48             Peruvian Restaurant             Pet Service   
70            Brazilian Restaurant              Soup Place   
83                     Coffee Shop  Furniture / Home Store   
85                             Gym   General Entertainment   
86                  Soccer Stadium          Clothing Store   
89                            Pier                Pie Shop   
91    

In [31]:
rio_merged.loc[rio_merged['Cluster Labels'] == 1, rio_merged.columns[[1] + list(range(5, rio_merged.shape[1]))]]

Latitude 2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1 -22.78506                   ATM           Pet Service           Pizza Place   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1                  Pier              Pie Shop    Photography Studio   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1              Pharmacy             Pet Store    Peruvian Restaurant

In [32]:
rio_merged.loc[rio_merged['Cluster Labels'] == 2, rio_merged.columns[[1] + list(range(5, rio_merged.shape[1]))]]

Latitude 2nd Most Common Venue 3rd Most Common Venue  \
35  -22.846575         Train Station            Food Truck   
102 -22.915193                   ATM  Kitchen Supply Store   
147 -22.991359        Scenic Lookout                   ATM   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
35   Gym / Fitness Center           Pet Service                  Pier   
102           Pizza Place                  Pier              Pie Shop   
147           Pet Service                  Pier              Pie Shop   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
35               Pie Shop    Photography Studio              Pharmacy   
102    Photography Studio              Pharmacy             Pet Store   
147    Photography Studio              Pharmacy             Pet Store   

    10th Most Common Venue  
35               Pet Store  
102            Pet Service  
147    Peruvian Restaurant

In [33]:
rio_merged.loc[rio_merged['Cluster Labels'] == 3, rio_merged.columns[[1] + list(range(5, rio_merged.shape[1]))]]

Latitude    2nd Most Common Venue              3rd Most Common Venue  \
0   -22.758926     Brazilian Restaurant                              Hotel   
2   -22.791759             Burger Joint                              Plaza   
3   -22.807506      American Restaurant                               Pier   
4   -22.797749                   Bakery                      Grocery Store   
5   -22.799960             Burger Joint                        Pet Service   
6   -22.796495                 Creperie                             Buffet   
7   -22.809533               Restaurant                       Samba School   
8   -22.805005                      Gym                           Gym Pool   
9   -22.810005      Japanese Restaurant                      Grocery Store   
11  -22.812193                      Bar                             Bakery   
13  -22.812836         Recording Studio                                Gym   
14  -22.816702           Ice Cream Shop                        Pizza Place   
17  -22.832642      Japanese Restaurant                        Pizza Place   
18  -22.821703        Accessories Store                Peruvian Restaurant   
19  -22.835113     Gym / Fitness Center                                Pub   
20  -22.823190           Farmers Market                                Gym   
21  -22.822153              Pizza Place                             Market   
22  -22.817128                   Bakery                         Food Truck   
23  -22.824700             Liquor Store                      Train Station   
24  -22.831888              Pizza Place                         Food Stand   
25  -22.838113                Drugstore                         Print Shop   
26  -22.821278      Japanese Restaurant                        Sports Club   
27  -22.825240      Japanese Restaurant                           Dive Bar   
28  -22.831874          Warehouse Store                         Playground   
30  -22.835169               Food Truck                       Soccer Field   
31  -22.834886                    Plaza                        Pizza Place   
32  -22.829624              Pizza Place                                Bar   
33  -22.838092       Athletics & Sports                Arts & Crafts Store   
34  -22.924312                      Bar               Brazilian Restaurant   
36  -22.304596                   Bakery               Gym / Fitness Center   
37  -22.843507              Pizza Place                                Bar   
39  -22.860348            Rugby Stadium                            Stadium   
43  -22.877274                    Plaza                           Pharmacy   
45  -22.859966              Snack Place                        Pizza Place   
46  -22.857180                    Plaza                                Spa   
50  -22.858972                      Gym                Martial Arts School   
51  -22.878813                      Bar               Fast Food Restaurant   
52  -22.866661                     Food                   Basketball Court   
53  -22.861663       Athletics & Sports                       Burger Joint   
54  -22.865932               Restaurant               Fast Food Restaurant   
55  -22.871548           Farmers Market                              Plaza   
56  -22.867698                  Factory                         Food Truck   
57  -22.875193           Ice Cream Shop  Southeastern Brazilian Restaurant   
58  -22.871658     Brazilian Restaurant                   Department Store   
59  -22.870527     Gym / Fitness Center                      Train Station   
60  -22.917625     Gym / Fitness Center                   Department Store   
61  -22.872512              Sports Club                             Bakery   
63  -22.870527              Supermarket                         Acai House   
64  -22.879519                   Museum                 Athletics & Sports   
66  -22.879676              Snack Place                                Gym   
67  -22.874392              

In [34]:
rio_merged.loc[rio_merged['Cluster Labels'] == 4, rio_merged.columns[[1] + list(range(5, rio_merged.shape[1]))]]

Latitude 2nd Most Common Venue 3rd Most Common Venue  \
10  -22.805249  Fast Food Restaurant  Brazilian Restaurant   
12  -22.819438  Brazilian Restaurant                Bakery   
16  -22.810408                 Plaza                 Diner   
29  -22.837621  Fast Food Restaurant           Beer Garden   
41  -22.850347                  Café                 Plaza   
42  -22.851976             Wine Shop                Bakery   
44  -22.853597          Burger Joint            Food Truck   
49  -22.860610  Fast Food Restaurant          Burger Joint   
62  -22.888752                   ATM           Pet Service   
65  -22.873999                   Gym        Ice Cream Shop   
79  -22.907805                   Gym           Snack Place   
80  -22.887507  Gym / Fitness Center          Burger Joint   
87  -22.913177          Burger Joint           Bus Station   
156 -22.851201                  Pool          Burger Joint   
162 -22.855678          Burger Joint              Pie Shop   

       4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
10                  Boutique  Gym / Fitness Center              Tea Room   
12         Food & Drink Shop         Women's Store                 Plaza   
16               Bus Station           Snack Place        Scenic Lookout   
29               Snack Place           Pizza Place                   Bar   
41             Grocery Store    Italian Restaurant              Pharmacy   
42             Grocery Store                   Gym                   ATM   
44        Chinese Restaurant  Gym / Fitness Center                   ATM   
49                 Cable Car   Arts & Crafts Store              Pharmacy   
62               Pizza Place                  Pier              Pie Shop   
65                 Pet Store  Gym / Fitness Center             Nightclub   
79                     Plaza                Bakery        Shopping Plaza   
80                  Pharmacy           Pizza Place                  Pier   
87                 Pet Store           Planetarium           Pizza Place   
156  Comfort Food Restaurant              Pharmacy           Planetarium   
162     Fast Food Restaurant              Pharmacy                   Gym   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
10               Pharmacy           Pizza Place                 Plaza   
12          Grocery Store           Music Venue  Gym / Fitness Center   
16          Boat or Ferry  Fast Food Restaurant    Photography Studio   
29                 Bakery        Ice Cream Shop            Food Truck   
41   Gym / Fitness Center        Ice Cream Shop           Pet Service   
42            Pet Service                  Pier              Pie Shop   
44               Pharmacy                  Pier              Pie Shop   
49     Athletics & Sports              Platform           Planetarium   
62     Photography Studio              Pharmacy             Pet Store   
65                Theater              Mountain             Pool Hall   
79         Ice Cream Shop        Farmers Market                Market   
80               Pie Shop    Photography Studio             Pet Store   
87                   Pier              Pie Shop    Photography Studio   
156           Pizza Place                  Pier              Pie Shop   
162    Salon / Barbershop             Juice Bar           Pastry Shop   

    10th Most Common Venue  
10        Sushi Restaurant  
12                Pharmacy  
16             Planetarium  
29    Gym / Fitness Center  
41                    Pier  
42      Photography Studio  
44      Photography Studio  
49             Pizza Place  
62     Peruvian Restaurant  
65                  Bakery  
79             Pet Service  
80                     ATM  
87                Pharmacy  
156     Photography Studio  
162       Pedestrian Plaza

# Selecting the best cluster and neighbourhoods

In [39]:
rio_merged[[c,'Cluster Labels', '1st Most Common Venue']].loc[rio_merged['1st Most Common Venue']  == 'Stakehouse']

Empty DataFrame
Columns: [Neighbourhood, Cluster Labels, 1st Most Common Venue]
Index: []

In [37]:
rio_merged[['Neighbourhood','Cluster Labels', '1st Most Common Venue']].loc[rio_merged['1st Most Common Venue']  == 'BBQ Joint']

Neighbourhood  Cluster Labels  \
77         Abolição, Rio de janeiro, RJ, Brazil               3   
88  Todos os Santos, Rio de janeiro, RJ, Brazil               3   

   1st Most Common Venue  
77             BBQ Joint  
88             BBQ Joint

In [38]:
rio_merged[['Neighbourhood','Cluster Labels', '1st Most Common Venue']].loc[rio_merged['1st Most Common Venue']  == 'Churrascaria']

Neighbourhood  Cluster Labels 1st Most Common Venue
21  Acari, Rio de janeiro, RJ, Brazil               3          Churrascaria

### <p> As stakehouses and BBQ in general are not the most common restaurant. </p>
&nbsp;
<p> Il Will use as rule to discard the clusters with strong cuncurrency in restaurant business, observing the concentration in the first four most common business. </p>
&nbsp;
<p> Clusters 4 is clearly the one with greater concentration of restaurants between the 3 most common columns. 3 is the one with more Stakehouse similar venues</p>
&nbsp;
<p> So, in the final intersection of the two methods, will select the neighbourhoods from remaining clusterd (0, 1, and 2) with high house income, to do a funnel with the options.</p>

# Retrieving, cleaning and exploring the social data

In [134]:
url = "https://pt.wikipedia.org/wiki/Lista_de_bairros_do_Rio_de_Janeiro_por_IDH"
teste = pd.read_html(url, header=0)
dft = teste[1]
dft.sample(20)

Nº    Bairro ou grupo de bairros Esperançade vidaao nascer(em anos)  \
65    64  São Cristóvão, Vasco da Gama                               7227   
123  119                    Santa Cruz                               6552   
103   99                        Pavuna                               6927   
68    67                     Madureira                               7097   
99    95           Vista Alegre, Irajá                               6281   
118  114                  Barros Filho                               6666   
67    66               Parque Anchieta                               7371   
119  115                      Inhoaíba                               6599   
95    92              Magalhães Bastos                               6890   
100   96                         Bangu                               6978   
30    30                     Freguesia                               7507   
92    89                      Realengo                               6963   
88    85                   Coelho Neto                               7086   
19    19               Todos os Santos                               7791   
57    57                    Praça Seca                               7170   
51    51                  Oswaldo Cruz                               7359   
89    86                  Padre Miguel                               7011   
35    35         Água Santa, Encantado                               7621   
76    75                     Itanhangá                               7028   
1      1          Barra da Tijuca, Joá                               8047   

    Taxa de alfabe-tização de adultos (%) Taxa bruta defrequência escolar (%)  \
65                                   9544                                8908   
123                                  9319                                7982   
103                                  9596                                8251   
68                                   9681                                9042   
99                                   9808                                9299   
118                                  9360                                8215   
67                                   9631                                8717   
119                                  9363                                8138   
95                                   9572                                9024   
100                                  9545                                8295   
30                                   9746                                9882   
92                                   9597                                8744   
88                                   9688                                8477   
19                                   9855                           108,20[a]   
57                                   9618                                9179   
51                                   9775                                9412   
89                                   9572                                8721   
35                                   9748                                9565   
76                                   9144                                7430   
1                                    9938                           110,09[a]   

    Renda per capita (em R$ de 2000) Índice de Longe-vidade  \
65                             41239                   0788   
123                            20623                   0675   
103                            28638                   0738   
68                             41981                   0766   
99                             47339                   0630   
118                            19896                   0694   
67                             35531                   0812   
119                            20761                   0683   
95                             31803                   0732   
100                            29655                   0

## Preprocessing

In [135]:
dft2 = dft[["Bairro ou grupo de bairros", "Renda per capita (em R$ de 2000)"]]
dft2.columns = ["Neighbourhood", "Income"]
dft3 = pd.DataFrame(dft2.Neighbourhood.str.split(',').tolist(), index=dft2.Income).stack()
dft3 = dft3.reset_index([0, 'Income'])
dft3.columns = dft3.iloc[0]
dft3.columns = ["Income", "Neighbourhood"]
dft3
dft3.drop(dft3.index[0], inplace = True)

In [136]:
dft3

Income                           Neighbourhood
1     2488,47[b]                         Barra da Tijuca
2     2488,47[b]                                     Joá
3    2139,56 [b]                                   Gávea
4     2441,28[b]                                  Leblon
5     1316,86[a]                        Jardim Guanabara
6     2465,45[b]                                 Ipanema
7     2955,29[b]                                   Lagoa
8     1781,71[b]                                Flamengo
9     1830,65[b]                                 Humaitá
10    1679,22[b]                             Laranjeiras
11    1952,77[b]                         Jardim Botânico
12    1623,42[b]                              Copacabana
13    1713,89[b]                                    Leme
14        137647                                Botafogo
15        137647                                    Urca
16        120673                                Maracanã
17        118328                                  Glória
18        113493                                  Grajaú
19        100016                                   Méier
20        120461                                  Tijuca
21        120461                       Alto da Boa Vista
22         82591                         Todos os Santos
23         76826                                    Anil
24         66934                           Vila da Penha
25         89707                                 Andaraí
26         71592                               Riachuelo
27         68494                                Campinho
28         68494                          Vila Valqueire
29         73040                                  Moneró
30         73040                              Portuguesa
31         82222                                  Catete
32         93125                             Vila Isabel
33         70905                                Cachambi
34         75128                               Pechincha
35         76682                               Freguesia
36        116618                Recreio dos Bandeirantes
37        116618                                 Grumari
38         63336                                  Centro
39         63336                                    Lapa
40         61441                            Higienópolis
41         70119                            Santa Teresa
42         70119                             Cosme Velho
43         49666                              Água Santa
44         49666                               Encantado
45         54429                                 Taquara
46         49882                             Vila Kosmos
47        113147                                 Vidigal
48        113147                             São Conrado
49         64031                             Cidade Nova
50         64031                       Praça da Bandeira
51         55299                              Bonsucesso
52         51828                                  Cocotá
53         51828                               Bancários
54         50540                          Maria da Graça
55         50540                            Del Castilho
56         52720                                 Ribeira
57         52720                                  Cacuia
58         58335                     Lins de Vasconcelos
59         57333                            Engenho Novo
60         51783                                   Zumbi
61         51783                            Pitangueiras
62         51783                       Praia da Bandeira
63         50876                                   Ramos
64         53654                       Engenho de Dentro
65         46723                                Abolição
66         46213                                 Deodoro
67         46213                            Vila Militar
68         46213                       Campo dos Afonsos
69         46213                          Jardim Sulacap
70         44134    

## Correcting bad formats

In [137]:
dft3["Income"]

1       2488,47[b]
2       2488,47[b]
3      2139,56 [b]
4       2441,28[b]
5       1316,86[a]
6       2465,45[b]
7       2955,29[b]
8       1781,71[b]
9       1830,65[b]
10      1679,22[b]
11      1952,77[b]
12      1623,42[b]
13      1713,89[b]
14          137647
15          137647
16          120673
17          118328
18          113493
19          100016
20          120461
21          120461
22           82591
23           76826
24           66934
25           89707
26           71592
27           68494
28           68494
29           73040
30           73040
31           82222
32           93125
33           70905
34           75128
35           76682
36          116618
37          116618
38           63336
39           63336
40           61441
41           70119
42           70119
43           49666
44           49666
45           54429
46           49882
47          113147
48          113147
49           64031
50           64031
51           55299
52           51828
53          

In [138]:
#Filtering non-number caracters in first Income fields
for v in range(1,14):
    dft3["Income"][v] = dft3["Income"][v][:-3]

dft3["Income"][3] = dft3["Income"][3][:-1]    
dft3

Income                           Neighbourhood
1    2488,47                         Barra da Tijuca
2    2488,47                                     Joá
3    2139,56                                   Gávea
4    2441,28                                  Leblon
5    1316,86                        Jardim Guanabara
6    2465,45                                 Ipanema
7    2955,29                                   Lagoa
8    1781,71                                Flamengo
9    1830,65                                 Humaitá
10   1679,22                             Laranjeiras
11   1952,77                         Jardim Botânico
12   1623,42                              Copacabana
13   1713,89                                    Leme
14    137647                                Botafogo
15    137647                                    Urca
16    120673                                Maracanã
17    118328                                  Glória
18    113493                                  Grajaú
19    100016                                   Méier
20    120461                                  Tijuca
21    120461                       Alto da Boa Vista
22     82591                         Todos os Santos
23     76826                                    Anil
24     66934                           Vila da Penha
25     89707                                 Andaraí
26     71592                               Riachuelo
27     68494                                Campinho
28     68494                          Vila Valqueire
29     73040                                  Moneró
30     73040                              Portuguesa
31     82222                                  Catete
32     93125                             Vila Isabel
33     70905                                Cachambi
34     75128                               Pechincha
35     76682                               Freguesia
36    116618                Recreio dos Bandeirantes
37    116618                                 Grumari
38     63336                                  Centro
39     63336                                    Lapa
40     61441                            Higienópolis
41     70119                            Santa Teresa
42     70119                             Cosme Velho
43     49666                              Água Santa
44     49666                               Encantado
45     54429                                 Taquara
46     49882                             Vila Kosmos
47    113147                                 Vidigal
48    113147                             São Conrado
49     64031                             Cidade Nova
50     64031                       Praça da Bandeira
51     55299                              Bonsucesso
52     51828                                  Cocotá
53     51828                               Bancários
54     50540                          Maria da Graça
55     50540                            Del Castilho
56     52720                                 Ribeira
57     52720                                  Cacuia
58     58335                     Lins de Vasconcelos
59     57333                            Engenho Novo
60     51783                                   Zumbi
61     51783                            Pitangueiras
62     51783                       Praia da Bandeira
63     50876                                   Ramos
64     53654                       Engenho de Dentro
65     46723                                Abolição
66     46213                                 Deodoro
67     46213                            Vila Militar
68     46213                       Campo dos Afonsos
69     46213                          Jardim Sulacap
70     44134                            Oswaldo Cruz
71     46031                                  Olaria
72     39985                           Bento Ribeiro
73     44764                                 Piedade
74     42467                       Quintino Bocaiúva
75     59026                   

In [139]:
dft3["Income"] = dft3["Income"].replace(",",'', regex=True)
dft3

Income                           Neighbourhood
1    248847                         Barra da Tijuca
2    248847                                     Joá
3    213956                                   Gávea
4    244128                                  Leblon
5    131686                        Jardim Guanabara
6    246545                                 Ipanema
7    295529                                   Lagoa
8    178171                                Flamengo
9    183065                                 Humaitá
10   167922                             Laranjeiras
11   195277                         Jardim Botânico
12   162342                              Copacabana
13   171389                                    Leme
14   137647                                Botafogo
15   137647                                    Urca
16   120673                                Maracanã
17   118328                                  Glória
18   113493                                  Grajaú
19   100016                                   Méier
20   120461                                  Tijuca
21   120461                       Alto da Boa Vista
22    82591                         Todos os Santos
23    76826                                    Anil
24    66934                           Vila da Penha
25    89707                                 Andaraí
26    71592                               Riachuelo
27    68494                                Campinho
28    68494                          Vila Valqueire
29    73040                                  Moneró
30    73040                              Portuguesa
31    82222                                  Catete
32    93125                             Vila Isabel
33    70905                                Cachambi
34    75128                               Pechincha
35    76682                               Freguesia
36   116618                Recreio dos Bandeirantes
37   116618                                 Grumari
38    63336                                  Centro
39    63336                                    Lapa
40    61441                            Higienópolis
41    70119                            Santa Teresa
42    70119                             Cosme Velho
43    49666                              Água Santa
44    49666                               Encantado
45    54429                                 Taquara
46    49882                             Vila Kosmos
47   113147                                 Vidigal
48   113147                             São Conrado
49    64031                             Cidade Nova
50    64031                       Praça da Bandeira
51    55299                              Bonsucesso
52    51828                                  Cocotá
53    51828                               Bancários
54    50540                          Maria da Graça
55    50540                            Del Castilho
56    52720                                 Ribeira
57    52720                                  Cacuia
58    58335                     Lins de Vasconcelos
59    57333                            Engenho Novo
60    51783                                   Zumbi
61    51783                            Pitangueiras
62    51783                       Praia da Bandeira
63    50876                                   Ramos
64    53654                       Engenho de Dentro
65    46723                                Abolição
66    46213                                 Deodoro
67    46213                            Vila Militar
68    46213                       Campo dos Afonsos
69    46213                          Jardim Sulacap
70    44134                            Oswaldo Cruz
71    46031                                  Olaria
72    39985                           Bento Ribeiro
73    44764                                 Piedade
74    42467                       Quintino Bocaiúva
75    59026                            Rio Comprido
76    49832                              Praça Seca
7

# Building the final neighbouhood recomendation list

In [149]:
dft3.dropna()

Income             Neighbourhood
1    248847           Barra da Tijuca
2    248847                       Joá
3    213956                     Gávea
4    244128                    Leblon
5    131686          Jardim Guanabara
6    246545                   Ipanema
7    295529                     Lagoa
8    178171                  Flamengo
9    183065                   Humaitá
10   167922               Laranjeiras
11   195277           Jardim Botânico
12   162342                Copacabana
13   171389                      Leme
14   137647                  Botafogo
15   137647                      Urca
16   120673                  Maracanã
17   118328                    Glória
18   113493                    Grajaú
19   100016                     Méier
20   120461                    Tijuca
21   120461         Alto da Boa Vista
22    82591           Todos os Santos
23    76826                      Anil
24    66934             Vila da Penha
25    89707                   Andaraí
26    71592                 Riachuelo
27    68494                  Campinho
28    68494            Vila Valqueire
29    73040                    Moneró
30    73040                Portuguesa
31    82222                    Catete
32    93125               Vila Isabel
33    70905                  Cachambi
34    75128                 Pechincha
35    76682                 Freguesia
36   116618  Recreio dos Bandeirantes
37   116618                   Grumari
38    63336                    Centro
39    63336                      Lapa
40    61441              Higienópolis
41    70119              Santa Teresa
42    70119               Cosme Velho
43    49666                Água Santa
44    49666                 Encantado
45    54429                   Taquara
46    49882               Vila Kosmos
47   113147                   Vidigal
48   113147               São Conrado
49    64031               Cidade Nova
50    64031         Praça da Bandeira
51    55299                Bonsucesso
52    51828                    Cocotá
53    51828                 Bancários
54    50540            Maria da Graça
55    50540              Del Castilho
56    52720                   Ribeira
57    52720                    Cacuia
58    58335       Lins de Vasconcelos
59    57333              Engenho Novo
60    51783                     Zumbi
61    51783              Pitangueiras
62    51783         Praia da Bandeira
63    50876                     Ramos
64    53654         Engenho de Dentro
65    46723                  Abolição
66    46213                   Deodoro
67    46213              Vila Militar
68    46213         Campo dos Afonsos
69    46213            Jardim Sulacap
70    44134              Oswaldo Cruz
71    46031                    Olaria
72    39985             Bento Ribeiro
73    44764                   Piedade
74    42467         Quintino Bocaiúva
75    59026              Rio Comprido
76    49832                Praça Seca
78    42612            Jardim América
79    51362                    Jacaré
80    51362                     Rocha
81    51362                   Sampaio
82    55735                 Freguesia
83    43633            Jardim Carioca
84    36262         Engenho da Rainha
85    39715              Brás de Pina
86    41239             São Cristóvão
87    41239             Vasco da Gama
88    42876                 Cascadura
89    35531           Parque Anchieta
90    41981                 Madureira
91    38981                   Pilares
92    43987                    Tanque
93    41305                   Estácio
94    36272                  Curicica
95    44477            Penha Circular
96    37665                   Benfica
97    45761                   Paquetá
98    65096                 Itanhangá
99    41619                      Tauá
101   33810             Rocha Miranda
102   36628           Marechal Hermes
103   33657                   Turiaçu
104   33689                 Guadalupe
105   32430                   Inhaúma
106   35111              Campo Grande
107   32864    

### Utilizing the 90% percentile

In [230]:
dft3["Income"] = dft3["Income"].astype(int)

In [446]:
dft3["Income"].describe()

count       160.000000
mean      61655.243750
std       51944.462298
min       17412.000000
25%       31577.000000
50%       45262.500000
75%       67324.000000
max      295529.000000
Name: Income, dtype: float64

In [447]:
# 50% percentile = 45262

## creating the candidate list by filtering the 90% quarter

In [479]:
rc_1 = dft3["Neighbourhood"].loc[dft3["Income"] > 45262]
rc_1 = pd.DataFrame(rc_1, columns=["Neighbourhood"])
rc_1

Neighbourhood
1             Barra da Tijuca
2                         Joá
3                       Gávea
4                      Leblon
5            Jardim Guanabara
6                     Ipanema
7                       Lagoa
8                    Flamengo
9                     Humaitá
10                Laranjeiras
11            Jardim Botânico
12                 Copacabana
13                       Leme
14                   Botafogo
15                       Urca
16                   Maracanã
17                     Glória
18                     Grajaú
19                      Méier
20                     Tijuca
21          Alto da Boa Vista
22            Todos os Santos
23                       Anil
24              Vila da Penha
25                    Andaraí
26                  Riachuelo
27                   Campinho
28             Vila Valqueire
29                     Moneró
30                 Portuguesa
31                     Catete
32                Vila Isabel
33                   Cachambi
34                  Pechincha
35                  Freguesia
36   Recreio dos Bandeirantes
37                    Grumari
38                     Centro
39                       Lapa
40               Higienópolis
41               Santa Teresa
42                Cosme Velho
43                 Água Santa
44                  Encantado
45                    Taquara
46                Vila Kosmos
47                    Vidigal
48                São Conrado
49                Cidade Nova
50          Praça da Bandeira
51                 Bonsucesso
52                     Cocotá
53                  Bancários
54             Maria da Graça
55               Del Castilho
56                    Ribeira
57                     Cacuia
58        Lins de Vasconcelos
59               Engenho Novo
60                      Zumbi
61               Pitangueiras
62          Praia da Bandeira
63                      Ramos
64          Engenho de Dentro
65                   Abolição
66                    Deodoro
67               Vila Militar
68          Campo dos Afonsos
69             Jardim Sulacap
71                     Olaria
75               Rio Comprido
76                 Praça Seca
79                     Jacaré
80                      Rocha
81                    Sampaio
82                  Freguesia
97                    Paquetá
98                  Itanhangá
124              Vista Alegre
125                     Irajá

## Filtering the clustering result list names

In [480]:
#Eliminating the 2 and 4 clusters

rio_f1 = rio_merged[['Neighbourhood', 'Cluster Labels']].loc[(rio_merged['Cluster Labels'] != 3) & (rio_merged['Cluster Labels'] != 4)]

In [481]:
rio_f1.drop("Cluster Labels", axis=1, inplace=True)

In [482]:
a = list(rio_f1[["Neighbourhood"][0]])

In [483]:
a

['Freguesia (Ilha), Rio de janeiro, RJ, Brazil',
 'Parque Colúmbia, Rio de janeiro, RJ, Brazil',
 'Honório Gurgel, Rio de janeiro, RJ, Brazil',
 'Maré, Rio de janeiro, RJ, Brazil',
 'Cidade Universitária, Rio de janeiro, RJ, Brazil',
 'Paciência, Rio de janeiro, RJ, Brazil',
 'Engenho da Rainha, Rio de janeiro, RJ, Brazil',
 'Piedade, Rio de janeiro, RJ, Brazil',
 'Benfica, Rio de janeiro, RJ, Brazil',
 'São Cristóvão, Rio de janeiro, RJ, Brazil',
 'Vasco da Gama, Rio de janeiro, RJ, Brazil',
 'Jacaré, Rio de janeiro, RJ, Brazil',
 'Rocha, Rio de janeiro, RJ, Brazil',
 'Tanque, Rio de janeiro, RJ, Brazil',
 'Cidade Nova, Rio de janeiro, RJ, Brazil',
 'Rio Comprido, Rio de janeiro, RJ, Brazil',
 'Estácio, Rio de janeiro, RJ, Brazil',
 'Gardênia Azul, Rio de janeiro, RJ, Brazil',
 'São Conrado, Rio de janeiro, RJ, Brazil',
 'Rocinha, Rio de janeiro, RJ, Brazil']

In [484]:
for i in range(len(a[:])):
    a[i] = a[i][:-28]
a = pd.DataFrame(a, columns=["Neighbourhood"])
a

Neighbourhood
0       Freguesia (Ilha)
1        Parque Colúmbia
2         Honório Gurgel
3                   Maré
4   Cidade Universitária
5              Paciência
6      Engenho da Rainha
7                Piedade
8                Benfica
9          São Cristóvão
10         Vasco da Gama
11                Jacaré
12                 Rocha
13                Tanque
14           Cidade Nova
15          Rio Comprido
16               Estácio
17         Gardênia Azul
18           São Conrado
19               Rocinha

## Intersecting the two lists

In [485]:
rio_final = rc_1.loc[rc_1['Neighbourhood'].isin(a['Neighbourhood'])]

In [486]:
rio_final

Neighbourhood
49   Cidade Nova
75  Rio Comprido
79        Jacaré

# Final Result

The Final result of the research, combining clustering os neighbourhoods with few stakehouses and similar menu restaurants and local population income above the mean of the city are: "Cidade Nova", "Rio Comprido" and "jacaré".